In [1]:
# Import required libraries and dependencies
import requests
import pandas as pd
import numpy as np
import scipy.stats as st
from pathlib import Path
import random

import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio

import warnings
warnings.filterwarnings('ignore')

pd.options.display.max_columns = None

In [2]:
# Loading data
file_path = Path("elements.csv")
df = pd.read_csv(file_path)


# Clean and Prepare data for optimization - get rid of suspended and injured players as well as players with low scores.
# Additionally adjust player costs given that we will only be selecting 11 players and not 15 as is typically the case in 
# fanatsy league

df = df.loc[(df['strength'] > 0.25)]
df = df.loc[(df['statusFull'] != 'susp')]
df = df.loc[(df['statusFull'] != 'inj')]
df['cost'] = df.apply(lambda x: round(x['now_cost']*(15/11),2),axis=1)
players = df[['web_name', 'position', 'team', 'description', 'cost', 'strength']]

In [3]:
players['stringCost'] = players.apply(lambda x: str(x['cost']), axis=1)
players['stringStrength'] = players.apply(lambda x: str(x['strength']), axis=1)

## Next we create variables that contain the count of players in each position as well as variables to keep count of players selected in each team

In [4]:
goalkeepers = players.loc[(players['position'] == 'Goalkeeper')]
goalkeepers.reset_index(inplace=True, drop=True)
gkNum = goalkeepers.shape[0] - 1

In [5]:
defenders = players.loc[(players['position'] == 'Defender')]
defenders.reset_index(inplace=True, drop=True)
defNum = defenders.shape[0] - 1

In [6]:
midfielders = players.loc[(players['position'] == 'Midfielder')]
midfielders.reset_index(inplace=True, drop=True)
midNum = midfielders.shape[0] - 1

In [7]:
forwards = players.loc[(players['position'] == 'Forward')]
forwards.reset_index(inplace=True, drop=True)
forNum = forwards.shape[0] - 1

In [8]:
#team count
Arsenal = 0
Aston_Villa = 0
Bournemouth = 0
Brentford = 0
Brighton = 0
Chelsea = 0
Crystal_Palace = 0
Everton = 0
Fulham = 0
Leeds = 0
Leicester = 0
Liverpool = 0
Man_City = 0
Man_United = 0
Newcastle = 0
Forest = 0
Southampton = 0
Tottenham = 0
West_Ham = 0
Wolves = 0

## Create functions to Optimize Team Selection

The rules of fanatsy league are such that the cost of a team cannot exceed 100 points and additionally no more than three players from the same EPL team can be selected. In addition, players are required to choose a set number of players for each position (GK, defenders, midfielders and forwards).

For our analysis we have set the teams to have 1 GK, 4 Defenders, 3 Midfielders and 3 Forwards - which is the typical formations applied by most EPL teams.

The following functions help to randomly pick players from each position and verify that more than 3 players have not been selected from the same team.

Since we are using random number generation, teams that cost most than 100 points were discarded.

In [9]:
#Funtion to randomly select a player for a particular position
def generateRandomNumber(Num):
    x =  random.randint(0, Num) 
    return x

In [10]:
#Based on the player randomly selected the team count is then updated
def updateTeam(Num, position, selected):
    
    num1 = generateRandomNumber(Num)
    
    while num1 in selected:
        num1 = generateRandomNumber(Num)
    
    selected.append(num1)
    
    x = position['team'][num1]
    
    if(x == 'Arsenal'):
        global Arsenal
        Arsenal += 1
    elif(x == 'Aston Villa'):
        global Aston_Villa
        Aston_Villa += 1
    elif(x == 'Bournemouth'):
        global Bournemouth
        Bournemouth += 1
    elif(x == 'Brentford'):
        global Brentford
        Brentford += 1
    elif(x == 'Brighton'):
        global Brighton
        Brighton += 1
    elif(x == 'Chelsea'):
        global Chelsea
        Chelsea += 1
    elif(x == 'Crystal Palace'):
        global Crystal_Palace
        Crystal_Palace += 1
    elif(x == 'Everton'):
        global Everton
        Everton += 1
    elif(x == 'Fulham'):
        global Fulham
        Fulham += 1
    elif(x == 'Leeds'):
        global Leeds
        Leeds += 1
    elif(x == 'Leicester'):
        global Leicester
        Leicester += 1
    elif(x == 'Liverpool'):
        global Liverpool
        Liverpool += 1
    elif(x == 'Man City'):
        global Man_City
        Man_City += 1
    elif(x == 'Man United'):
        global Man_United
        Man_United +=1
    elif(x == 'Newcastle'):
        global Newcastle
        Newcastle +=1
    elif(x == "Nott'm Forest"):
        global Forest
        Forest += 1
    elif(x == 'Southampton'):
        global Southampton
        Southampton += 1
    elif(x == 'Tottenham'):
        global Tottenham
        Tottenham += 1
    elif(x == 'West Ham'):
        global West_Ham
        West_Ham += 1
    elif(x == 'Wolves'):
        global Wolves
        Wolves += 1
    
    return num1

In [11]:
#The last function verifies that more than 4 players have not been selected from the same EPL team. If they have then
#that player selection is discarded and a new player is selected and checked until that all rules have been met.
def verify(Num, position, selected):
    
    x = updateTeam(Num, position, selected)
    
    global Arsenal
    while(Arsenal > 4):
        Arsenal -= 1
        selected = selected[:-1]
        x = updateTeam(Num, position, selected)
    
    global Aston_Villa
    while(Aston_Villa > 4):
        Aston_Villa -= 1
        selected = selected[:-1]
        x = updateTeam(Num, position, selected)
    
    global Bournemouth
    while(Bournemouth > 4):
        Bournemouth -= 1
        selected = selected[:-1]
        x = updateTeam(Num, position, selected)
    
    global Brentford
    while(Brentford> 4):
        Brentford -= 1
        selected = selected[:-1]
        x = updateTeam(Num, position, selected)
    
    global Brighton
    while(Brighton > 4):
        Brighton -= 1
        selected = selected[:-1]
        x = updateTeam(Num, position, selected)
    
    global Chelsea
    while(Chelsea > 4):
        Chelsea -= 1
        selected = selected[:-1]
        x = updateTeam(Num, position, selected)
    
    global Crystal_Palace
    while(Crystal_Palace > 4):
        Crystal_Palace -= 1
        selected = selected[:-1]
        x = updateTeam(Num, position, selected)
    
    global Everton
    while(Everton > 4):  
        Everton -= 1
        selected = selected[:-1]
        x = updateTeam(Num, position, selected)
    
    global Fulham  
    while(Fulham > 4):
        Fulham -= 1
        selected = selected[:-1]
        x = updateTeam(Num, position, selected)
    
    global Leeds 
    while(Leeds > 4):
        Leeds -= 1
        selected = selected[:-1]
        x = updateTeam(Num, position, selected)
    
    global Leicester
    while(Leicester > 4):
        Leicester -= 1
        selected = selected[:-1]
        x = updateTeam(Num, position, selected)
    
    global Liverpool
    while(Liverpool > 4):
        Liverpool -= 1
        selected = selected[:-1]
        x = updateTeam(Num, position, selected)     
    
    global Man_City
    while(Man_City > 4):
        Man_City -= 1
        selected = selected[:-1]
        x = updateTeam(Num, position, selected)
    
    global Man_United
    while(Man_United > 4):
        Man_United -= 1
        selected = selected[:-1]
        x = updateTeam(Num, position, selected)
    
    global Newcastle
    while(Newcastle > 4):
        Newcastle -= 1
        selected = selected[:-1]
        x = updateTeam(Num, position, selected)
    
    global Forest
    while(Forest > 4):
        Forest -= 1
        selected = selected[:-1]
        x = updateTeam(Num, position, selected)
    
    global Southampton
    while(Southampton > 4):
        Southampton -= 1
        selected = selected[:-1]
        x = updateTeam(Num, position, selected)
    
    global Tottenham
    while(Tottenham > 4): 
        Tottenham -= 1
        selected = selected[:-1]
        x = updateTeam(Num, position, selected)
    
    global West_Ham
    while(West_Ham > 4):
        West_Ham -= 1
        selected = selected[:-1]
        x = updateTeam(Num, position, selected)
    
    global Wolves
    while(Wolves > 4):
        Wolves -= 1
        selected = selected[:-1]
        x = updateTeam(Num, position, selected)
    
    return x
    

## Simulate all teams

The follwing block of code generates 100,000 randomly selected teams according to the criteria/rules outlined above. Teams costing more tha 100 points were discard.

For teams meeting the criteria, team scores and costs were appended into an empty for further analysis

In [12]:
count = 100000

# team lists
allteamPlayers = []
allteamPlayersTeam = []
allteamPlayerDescription = []
allteamPlayerPosition = []
allteamCost = []
allteamStrength = []
allNumCost = []
allNumStrength = []

for i in range(0, count):
    
    #team count
    Arsenal = 0
    Aston_Villa = 0
    Bournemouth = 0
    Brentford = 0
    Brighton = 0
    Chelsea = 0
    Crystal_Palace = 0
    Everton = 0
    Fulham = 0
    Leeds = 0
    Leicester = 0
    Liverpool = 0
    Man_City = 0
    Man_United = 0
    Newcastle = 0
    Forest = 0
    Southampton = 0
    Tottenham = 0
    West_Ham = 0
    Wolves = 0
    
    # selected players
    selectedGK = []
    selectedDefenders = []
    selectedMidfielders = []
    selectedForwards = []
    
    # empty lists
    teamPlayers = []
    teamPlayersTeam = []
    teamPlayerDescription = []
    teamPlayerPosition = []
    teamCost = []
    teamStrength = []
    
    
    #Player 1 (Defender 1)
    def1 = verify(defNum, defenders, selectedDefenders)
    teamPlayersTeam.append(defenders['team'][def1])
    teamPlayers.append(defenders['web_name'][def1])
    teamPlayerDescription.append(defenders['description'][def1])
    teamPlayerPosition.append(defenders['position'][def1])
    teamCost.append((defenders['stringCost'][def1]))
    teamStrength.append(defenders['stringStrength'][def1])

    #Player 2 (Midfielder 1)
    mid1 = verify(midNum, midfielders, selectedMidfielders)
    teamPlayersTeam.append(midfielders['team'][mid1])
    teamPlayers.append(midfielders['web_name'][mid1])
    teamPlayerDescription.append(midfielders['description'][mid1])
    teamPlayerPosition.append(midfielders['position'][mid1])
    teamCost.append((midfielders['stringCost'][mid1]))
    teamStrength.append(midfielders['stringStrength'][mid1])

    #Player 3 (Forward 1)
    for1 = verify(forNum, forwards, selectedForwards)
    teamPlayersTeam.append(forwards['team'][for1])
    teamPlayers.append(forwards['web_name'][for1])
    teamPlayerDescription.append(forwards['description'][for1])
    teamPlayerPosition.append(forwards['position'][for1])
    teamCost.append((forwards['stringCost'][for1]))
    teamStrength.append(forwards['stringStrength'][for1])

    #Player 4 (Goalkeeper)
    gk = verify(gkNum, goalkeepers, selectedGK)
    teamPlayersTeam.append(goalkeepers['team'][gk])
    teamPlayers.append(goalkeepers['web_name'][gk])
    teamPlayerDescription.append(goalkeepers['description'][gk])
    teamPlayerPosition.append(goalkeepers['position'][gk])
    teamCost.append((goalkeepers['stringCost'][gk]))
    teamStrength.append(goalkeepers['stringStrength'][gk])

    #Player 5 (Defender 2)
    def2 = verify(defNum, defenders, selectedDefenders)
    teamPlayersTeam.append(defenders['team'][def2])
    teamPlayers.append(defenders['web_name'][def2])
    teamPlayerDescription.append(defenders['description'][def2])
    teamPlayerPosition.append(defenders['position'][def2])
    teamCost.append((defenders['stringCost'][def2]))
    teamStrength.append(defenders['stringStrength'][def2])

    #Player 6 (Midfielder 2)
    mid2 = verify(midNum, midfielders, selectedMidfielders)
    teamPlayersTeam.append(midfielders['team'][mid2])
    teamPlayers.append(midfielders['web_name'][mid2])
    teamPlayerDescription.append(midfielders['description'][mid2])
    teamPlayerPosition.append(midfielders['position'][mid2])
    teamCost.append((midfielders['stringCost'][mid2]))
    teamStrength.append(midfielders['stringStrength'][mid2])

    #Player 7 (Forward 2)
    for2 = verify(forNum, forwards, selectedForwards)
    teamPlayersTeam.append(forwards['team'][for2])
    teamPlayers.append(forwards['web_name'][for2])
    teamPlayerDescription.append(forwards['description'][for2])
    teamPlayerPosition.append(forwards['position'][for2])
    teamCost.append((forwards['stringCost'][for2]))
    teamStrength.append(forwards['stringStrength'][for2])

    #Player 8 (Defender 3)
    def3 = verify(defNum, defenders, selectedDefenders)
    teamPlayersTeam.append(defenders['team'][def3])
    teamPlayers.append(defenders['web_name'][def3])
    teamPlayerDescription.append(defenders['description'][def3])
    teamPlayerPosition.append(defenders['position'][def3])
    teamCost.append((defenders['stringCost'][def3]))
    teamStrength.append(defenders['stringStrength'][def3])

    #Player 9 (Midfielder 3)
    mid3 = verify(midNum, midfielders, selectedMidfielders)
    teamPlayersTeam.append(midfielders['team'][mid3])
    teamPlayers.append(midfielders['web_name'][mid3])
    teamPlayerDescription.append(midfielders['description'][mid3])
    teamPlayerPosition.append(midfielders['position'][mid3])
    teamCost.append((midfielders['stringCost'][mid3]))
    teamStrength.append(midfielders['stringStrength'][mid3])

    #Player 10 (Forward 3)
    for3 = verify(forNum, forwards, selectedForwards)
    teamPlayersTeam.append(forwards['team'][for3])
    teamPlayers.append(forwards['web_name'][for3])
    teamPlayerDescription.append(forwards['description'][for3])
    teamPlayerPosition.append(forwards['position'][for3])
    teamCost.append((forwards['stringCost'][for3]))
    teamStrength.append(forwards['stringStrength'][for3])


    #Player 11 (Defender 4)
    def4 = verify(defNum, defenders, selectedDefenders)
    teamPlayersTeam.append(defenders['team'][def4])
    teamPlayers.append(defenders['web_name'][def4])
    teamPlayerDescription.append(defenders['description'][def4])
    teamPlayerPosition.append(defenders['position'][def4])
    teamCost.append((defenders['stringCost'][def4]))
    teamStrength.append(defenders['stringStrength'][def4])
    
    
    value = round(sum(list(np.float_(teamCost))),2)
    score = round(sum(list(np.float_(teamStrength))),5)
    
    if(value <= 100):
    
        allteamPlayers.append(teamPlayers)
        allteamPlayersTeam.append(teamPlayersTeam)
        allteamPlayerDescription.append(teamPlayerDescription)
        allteamPlayerPosition.append(teamPlayerPosition)
        allteamCost.append(teamCost)
        allteamStrength.append(teamStrength)
        allNumCost.append(value)
        allNumStrength.append(score)
    
    i += 1

In [13]:
#----------------------------

## Team Anaysis

Our Optimization analysis shows that the greatest team strenghth comes out at 5.6 and was obtained by the 44,190 team selected from our random team generator with the team cost coming out at 99.16 points.

In [14]:
max_strength = max(allNumStrength)
maxStrength_index = allNumStrength.index(max_strength)

In [15]:
max_strength

5.60398

In [16]:
maxStrength_index

44190

In [17]:
teamCost = allNumCost[maxStrength_index]
teamCost

99.16

## Dream Team Analysis

The below shows the optimal team selected, i.e. the Dream Team. The cells show the players, the EPL teams they represent.
In addition, we also obtain the players position as well as their score and cost.

In [18]:
#Players in Dream Team
allteamPlayers[maxStrength_index]

['Trippier',
 'Ødegaard',
 'Haaland',
 'Pope',
 'Tarkowski',
 'Rashford',
 'Toney',
 'Saliba',
 'Almirón',
 'Mitrović',
 'Mee']

In [19]:
#EPL teams represented by selected players
allteamPlayersTeam[maxStrength_index]

['Newcastle',
 'Arsenal',
 'Man City',
 'Newcastle',
 'Everton',
 'Man United',
 'Brentford',
 'Arsenal',
 'Newcastle',
 'Fulham',
 'Brentford']

In [20]:
#Conenation/Description of players and teams
allteamPlayerDescription[maxStrength_index]

['[Trippier, Newcastle]',
 '[Ødegaard, Arsenal]',
 '[Haaland, Man City]',
 '[Pope, Newcastle]',
 '[Tarkowski, Everton]',
 '[Rashford, Man United]',
 '[Toney, Brentford]',
 '[Saliba, Arsenal]',
 '[Almirón, Newcastle]',
 '[Mitrović, Fulham]',
 '[Mee, Brentford]']

In [21]:
#Positions of players selected
allteamPlayerPosition[maxStrength_index]

['Defender',
 'Midfielder',
 'Forward',
 'Goalkeeper',
 'Defender',
 'Midfielder',
 'Forward',
 'Defender',
 'Midfielder',
 'Forward',
 'Defender']

In [22]:
#Player Costs
allteamCost[maxStrength_index]

['8.32',
 '9.55',
 '16.64',
 '7.5',
 '5.73',
 '9.82',
 '10.5',
 '7.23',
 '7.77',
 '9.55',
 '6.55']

In [23]:
#Player Scores
allteamStrength[maxStrength_index]

['0.82059',
 '0.58175',
 '1.0',
 '0.33495',
 '0.28269',
 '0.55671',
 '0.4931',
 '0.34645',
 '0.45399',
 '0.37689',
 '0.35686']

## Team Distributions

The code and cells below plot the scatter plot (team strength vs. cost) for each of the teams randomly selected and shows where the optimal (dream team) is. In addition we also plot the histogram of team scores.

In [24]:
dictionary = {'Strength': allNumStrength, 'Cost': allNumCost}
optimalTeams = pd.DataFrame(data=dictionary)

In [25]:
# Scatter Plot with optimal Team
fig5 = px.scatter(optimalTeams, x='Cost', y='Strength', color='Strength', 
                  )
fig5.add_trace(go.Scatter(x=[teamCost], y=[max_strength], name='Optimal Team',
            marker=dict(
            color='LightSkyBlue',
            size=20,
            )))

fig5.update_layout(legend=dict(
    orientation="h",
    yanchor="top",
    y=1.1,
    xanchor="right",
    x=1
    ),
    template='seaborn',
    margin=dict (l=0, r=0, t=0, b=0)
)

In [26]:
# Normal Histogram of team strengths
fig1 = go.Figure(data=[go.Histogram(x=optimalTeams['Strength'], histnorm='probability')])
fig1.show()

In [27]:
percentile99 = sorted(allNumStrength)[-1000]
percentile99

5.1445

In [28]:
percentile99_index = allNumStrength.index(percentile99)
percentile99_index

22776